# Geocoding Data Using Google API

### Import Packages

In [13]:
import pandas as pd
import requests
import logging
import time

In [14]:
logger = logging.getLogger("root")
logger.setLevel(logging.DEBUG)
ch = logging.StreamHandler()
ch.setLevel(logging.DEBUG)
logger.addHandler(ch)

### Set Up Google API Key

In [36]:
API_KEY = 

In [16]:
# Minutes to wait between google pings when limit is reached
BACKOFF_TIME = 30

In [30]:
# Output and Input file name
output_filename = '../data/geocode_address.csv'
input_filename = '../data/address.csv'
RETURN_FULL_RESULTS = False

In [31]:
data = pd.read_csv(input_filename, encoding = 'utf8')
addresses = (data['concat_address']).tolist()

### Extracting geocode results from API

In [40]:
def get_google_results(address, return_full_response = False):
    '''
    Gets geocode results from API
    
    address: string address input
    return_full_response: boolean to determine if you want entire jsonfile
    
    Returns address, latitiude, longitude, accuracy, google_place_id, type, postcode'''
    
    geocode_url = "https://maps.googleapis.com/maps/api/geocode/json?address={}&key=API_KEY".format(address)
        
    r = requests.get(geocode_url)
    json_data = r.json()
    
    # If there are not results or an error, it returns empty results
    if len(json_data['results']) == 0:
        output = {
            'formatted_address' : None,
            'latitude' : None,
            'longitude' : None,
            'accuracy' : None,
            'google_place_id' : None,
            'type' : None,
            'postcode' : None
        }
    else:
        answer = json_data['results'][0]
        output = {
           'formatted_address' : answer.get('formatted_address'),
            'latitude' : answer.get('geometry').get('location').get('lat'),
            'longitude' : answer.get('geometry').get('location').get('lng'),
            'accuracy' : answer.get('geometry').get('location').get('location_type'),
            'google_place_id' : answer.get('place_id'),
            'type' : ','.join(answer.get('types')),
            'postcode': ','.join([x['long_name'] for x in answer.get('address_components') if 'postal_code' in x.get('types')])
        }
    
    # Append address and status
    output['input_string'] = address
    output['number_of_results'] = len(json_data['results'])
    output['status'] = json_data.get('status')
    if return_full_response is True:
        output['response'] = results
    
    return output

In [35]:
a = addresses[1]
type(a)


'15553 E VALLEY BLVD, LA PUENTE, CA 91744'

In [41]:
# Test one address to see if API Key is valid 
test_result = get_google_results(a, RETURN_FULL_RESULTS)
print(test_result)

{'formatted_address': '15553 Valley Blvd, La Puente, CA 91744, USA', 'latitude': 34.0206291, 'longitude': -117.9587373, 'accuracy': None, 'google_place_id': 'ChIJaRtAtXDWwoARbknsWm3KnKk', 'type': 'premise', 'postcode': '91744', 'input_string': '15553 E VALLEY BLVD, LA PUENTE, CA 91744', 'number_of_results': 1, 'status': 'OK'}


In [44]:
# Create DataFrame for Results

results = []

for address in addresses:
    geocoded = False
    while geocoded is not True:
        # Geocode address with google
        try:
            geocode_result = get_google_results(address,RETURN_FULL_RESULTS)
        except Exception as e:
            logger.exception(e)
            logger.error("Major error with {}".format(address))
            logger.error("Skipping!")
            geocoded = True
        if geocode_result['status'] == 'OVER_QUERY_LIMIT':
            logger.info("Query Limit Hit")
            time.sleep(BACKOFF_TIME * 60)
            geocoded = False
        else:
            if geocode_result['status'] != 'OK':
                logger.warning('Error geocoding {}: {}'.format(address, geocode_result['status']))
            logger.debug('Geocoded: {}: {}'.format(address, geocode_result['status']))
            results.append(geocode_result)
            geocoded = True
            

    if len(results) % 500 == 0:
        pd.DataFrame(results).to_csv("{}_bak".format(output_filename))

logger.info('Finished geocoding all addresses')

# Convert list result to dataframe
pd.DataFrame(results).to_csv(output_filename, encoding = 'utf8')
            

Geocoded: 24301 CRENSHAW BLVD, TORRANCE, CA 90505: OK
Geocoded: 24301 CRENSHAW BLVD, TORRANCE, CA 90505: OK
Geocoded: 15553 E VALLEY BLVD, LA PUENTE, CA 91744: OK
Geocoded: 15553 E VALLEY BLVD, LA PUENTE, CA 91744: OK
Error geocoding 18912 E GALE AVE STE #A, ROWLAND HEIGHTS, CA 91748: REQUEST_DENIED
Error geocoding 18912 E GALE AVE STE #A, ROWLAND HEIGHTS, CA 91748: REQUEST_DENIED
Geocoded: 18912 E GALE AVE STE #A, ROWLAND HEIGHTS, CA 91748: REQUEST_DENIED
Geocoded: 18912 E GALE AVE STE #A, ROWLAND HEIGHTS, CA 91748: REQUEST_DENIED
Geocoded: 3614 MLK JR BLVD, LYNWOOD, CA 90262: OK
Geocoded: 3614 MLK JR BLVD, LYNWOOD, CA 90262: OK
Geocoded: 17198 S NORWALK BLVD, CERRITOS, CA 90703: OK
Geocoded: 17198 S NORWALK BLVD, CERRITOS, CA 90703: OK
Geocoded: 1320 N VINE ST, LOS ANGELES, CA 90038: OK
Geocoded: 1320 N VINE ST, LOS ANGELES, CA 90038: OK
Error geocoding 7445 SUNSET BLVD # B, LOS ANGELES, CA 90046: REQUEST_DENIED
Error geocoding 7445 SUNSET BLVD # B, LOS ANGELES, CA 90046: REQUEST_DEN

Geocoded: 5626 E WHITTIER, COMMERCE, CA 90022: OK
Geocoded: 5626 E WHITTIER, COMMERCE, CA 90022: OK
Geocoded: 6000 E FLORENCE ST STE B-C, BELL GARDENS, CA 90201: OK
Geocoded: 6000 E FLORENCE ST STE B-C, BELL GARDENS, CA 90201: OK
Geocoded: 19927 GOLDEN VALLEY RD, SANTA CLARITA, CA 91321: OK
Geocoded: 19927 GOLDEN VALLEY RD, SANTA CLARITA, CA 91321: OK
Geocoded: 3944 N PECK RD A1, EL MONTE, CA 91731: OK
Geocoded: 3944 N PECK RD A1, EL MONTE, CA 91731: OK
Geocoded: 3444 E MLK JR BLVD, LYNWOOD, CA 90262: OK
Geocoded: 3444 E MLK JR BLVD, LYNWOOD, CA 90262: OK
Geocoded: 11340 E 183RD ST, ARTESIA, CA 90701: OK
Geocoded: 11340 E 183RD ST, ARTESIA, CA 90701: OK
Geocoded: 2401 E WHITTIER BLVD, LOS ANGELES, CA 90023: OK
Geocoded: 2401 E WHITTIER BLVD, LOS ANGELES, CA 90023: OK
Geocoded: 794 MISSION BLVD, POMONA, CA 91766: OK
Geocoded: 794 MISSION BLVD, POMONA, CA 91766: OK
Geocoded: 2536 S FIGUEROA ST, LOS ANGELES, CA 90007: OK
Geocoded: 2536 S FIGUEROA ST, LOS ANGELES, CA 90007: OK
Geocoded: 13

Geocoded: 4 GREEN PLEASURE PIER, AVALON, CA 90704: OK
Geocoded: 231 9TH ST, LOS ANGELES, CA 90015: OK
Geocoded: 231 9TH ST, LOS ANGELES, CA 90015: OK
Error geocoding 1 N INDIAN HL # D-104, CLAREMONT, CA 91711: REQUEST_DENIED
Error geocoding 1 N INDIAN HL # D-104, CLAREMONT, CA 91711: REQUEST_DENIED
Geocoded: 1 N INDIAN HL # D-104, CLAREMONT, CA 91711: REQUEST_DENIED
Geocoded: 1 N INDIAN HL # D-104, CLAREMONT, CA 91711: REQUEST_DENIED
Error geocoding 2310 PASADENA AVE STE # 102, LOS ANGELES, CA 90031: REQUEST_DENIED
Error geocoding 2310 PASADENA AVE STE # 102, LOS ANGELES, CA 90031: REQUEST_DENIED
Geocoded: 2310 PASADENA AVE STE # 102, LOS ANGELES, CA 90031: REQUEST_DENIED
Geocoded: 2310 PASADENA AVE STE # 102, LOS ANGELES, CA 90031: REQUEST_DENIED
Geocoded: 811 W 7TH ST, LOS ANGELES, CA 90017: OK
Geocoded: 811 W 7TH ST, LOS ANGELES, CA 90017: OK
Geocoded: 11629 E VALLEY BLVD, EL MONTE, CA 91783: OK
Geocoded: 11629 E VALLEY BLVD, EL MONTE, CA 91783: OK
Geocoded: 7851 FOOTHILL BLVD, SUNL

Geocoded: 15436 E WHITTIER BLVD, WHITTIER, CA 90603: OK
Geocoded: 15436 E WHITTIER BLVD, WHITTIER, CA 90603: OK
Geocoded: 2035 N VERDUGO BLVD, MONTROSE, CA 91203: OK
Geocoded: 2035 N VERDUGO BLVD, MONTROSE, CA 91203: OK
Geocoded: 11928 GARVEY AVE, SOUTH EL MONTE, CA 91733: OK
Geocoded: 11928 GARVEY AVE, SOUTH EL MONTE, CA 91733: OK
Geocoded: 24 W SIERRA MADRE, SIERRA MADRE, CA 91024: OK
Geocoded: 24 W SIERRA MADRE, SIERRA MADRE, CA 91024: OK
Geocoded: 9301 E WHITTIER BLVD, PICO RIVERA, CA 90660: OK
Geocoded: 9301 E WHITTIER BLVD, PICO RIVERA, CA 90660: OK
Geocoded: 14740 S BEACH BLVD, LA MIRADA, CA 90638: OK
Geocoded: 14740 S BEACH BLVD, LA MIRADA, CA 90638: OK
Geocoded: 15126 S WESTERN, GARDENA, CA 90249: OK
Geocoded: 15126 S WESTERN, GARDENA, CA 90249: OK
Geocoded: 2704 E CARSON ST, LAKEWOOD, CA 90712: OK
Geocoded: 2704 E CARSON ST, LAKEWOOD, CA 90712: OK
Geocoded: 3962 W ARTESIA BLVD, TORRANCE, CA 90504: OK
Geocoded: 3962 W ARTESIA BLVD, TORRANCE, CA 90504: OK
Error geocoding 3650 W

Geocoded: 16023 E AMAR RD, LA PUENTE, CA 91744: OK
Geocoded: 8500 BALBOA BLVD, VAN NUYS, CA 91406: OK
Geocoded: 8500 BALBOA BLVD, VAN NUYS, CA 91406: OK
Geocoded: 8225 BEVERLY BLVD, LOS ANGELES, CA 90048: OK
Geocoded: 8225 BEVERLY BLVD, LOS ANGELES, CA 90048: OK
Geocoded: 1141 E BROADWAY AVE, GLENDALE, CA 91205: OK
Geocoded: 1141 E BROADWAY AVE, GLENDALE, CA 91205: OK
Geocoded: 12972 E LAKELAND RD, SANTA FE SPRINGS, CA 90670: OK
Geocoded: 12972 E LAKELAND RD, SANTA FE SPRINGS, CA 90670: OK
Geocoded: 18614 S PIONEER BLVD, ARTESIA, CA 90701: OK
Geocoded: 18614 S PIONEER BLVD, ARTESIA, CA 90701: OK
Geocoded: 4131 WOODRUFF AVE, BELLFLOWER, CA 90713: OK
Geocoded: 4131 WOODRUFF AVE, BELLFLOWER, CA 90713: OK
Geocoded: 2223 BEVERLY, LOS ANGELES, CA 90057: OK
Geocoded: 2223 BEVERLY, LOS ANGELES, CA 90057: OK
Error geocoding 10201 RESEDA BLVD # 102, RESEDA, CA 91324: REQUEST_DENIED
Error geocoding 10201 RESEDA BLVD # 102, RESEDA, CA 91324: REQUEST_DENIED
Geocoded: 10201 RESEDA BLVD # 102, RESEDA

...

Error geocoding 10250 SANTA MONICA BLVD # 2010, CENTURY CITY, CA 90067: REQUEST_DENIED
Error geocoding 10250 SANTA MONICA BLVD # 2010, CENTURY CITY, CA 90067: REQUEST_DENIED
Geocoded: 10250 SANTA MONICA BLVD # 2010, CENTURY CITY, CA 90067: REQUEST_DENIED
Geocoded: 10250 SANTA MONICA BLVD # 2010, CENTURY CITY, CA 90067: REQUEST_DENIED
Geocoded: 3255 W BEVERLY BLVD, LOS ANGELES, CA 90057: OK
Geocoded: 3255 W BEVERLY BLVD, LOS ANGELES, CA 90057: OK
Geocoded: 16460 WHITTIER BLVD, WHITTIER, CA 90603: OK
Geocoded: 16460 WHITTIER BLVD, WHITTIER, CA 90603: OK
Error geocoding 6160 N LAUREL CANYON BLVD # 120, NORTH HOLLYWOOD, CA 91606: REQUEST_DENIED
Error geocoding 6160 N LAUREL CANYON BLVD # 120, NORTH HOLLYWOOD, CA 91606: REQUEST_DENIED
Geocoded: 6160 N LAUREL CANYON BLVD # 120, NORTH HOLLYWOOD, CA 91606: REQUEST_DENIED
Geocoded: 6160 N LAUREL CANYON BLVD # 120, NORTH HOLLYWOOD, CA 91606: REQUEST_DENIED
Geocoded: 10450 ARTESIA BLVD, BELLFLOWER, CA 90706: OK
Geocoded: 10450 ARTESIA BLVD, BELLF

Geocoded: 10893 SAN FERNANDO RD, PACOIMA, CA 91331: OK
Geocoded: 10893 SAN FERNANDO RD, PACOIMA, CA 91331: OK
Geocoded: 2024 SAWTELLE BLVD, LOS ANGELES, CA 90025: OK
Geocoded: 2024 SAWTELLE BLVD, LOS ANGELES, CA 90025: OK
Geocoded: 6160 LAUREL CANYON BLVD STE 175, NORTH HOLLYWOOD, CA 91606: OK
Geocoded: 6160 LAUREL CANYON BLVD STE 175, NORTH HOLLYWOOD, CA 91606: OK
Geocoded: 56 E DUARTE, ARCADIA, CA 91006: OK
Geocoded: 56 E DUARTE, ARCADIA, CA 91006: OK
Geocoded: 906 E COLORADO, GLENDALE, CA 91205: OK
Geocoded: 906 E COLORADO, GLENDALE, CA 91205: OK
Error geocoding 10642 BALBOA BLVD # B, GRANADA HILLS, CA 91344: REQUEST_DENIED
Error geocoding 10642 BALBOA BLVD # B, GRANADA HILLS, CA 91344: REQUEST_DENIED
Geocoded: 10642 BALBOA BLVD # B, GRANADA HILLS, CA 91344: REQUEST_DENIED
Geocoded: 10642 BALBOA BLVD # B, GRANADA HILLS, CA 91344: REQUEST_DENIED
Geocoded: 15300 S FIGUEROA ST STE B, GARDENA, CA 90248: OK
Geocoded: 15300 S FIGUEROA ST STE B, GARDENA, CA 90248: OK
Error geocoding 19350 

Error geocoding 27131 SIERRA HWY # 120-A, SANTA CLARITA, CA 91351: REQUEST_DENIED
Error geocoding 27131 SIERRA HWY # 120-A, SANTA CLARITA, CA 91351: REQUEST_DENIED
Geocoded: 27131 SIERRA HWY # 120-A, SANTA CLARITA, CA 91351: REQUEST_DENIED
Geocoded: 27131 SIERRA HWY # 120-A, SANTA CLARITA, CA 91351: REQUEST_DENIED
Geocoded: 3405 W BEVERLY BLVD STE B, MONTEBELLO, CA 90640: OK
Geocoded: 3405 W BEVERLY BLVD STE B, MONTEBELLO, CA 90640: OK
Geocoded: 1831 S LA CIENEGA BLVD, LOS ANGELES, CA 90035: OK
Geocoded: 1831 S LA CIENEGA BLVD, LOS ANGELES, CA 90035: OK
Geocoded: 38575 6TH ST E, PALMDALE, CA 93550: OK
Geocoded: 38575 6TH ST E, PALMDALE, CA 93550: OK
Geocoded: 3501 W SUNSET BLVD, LOS ANGELES, CA 90026: OK
Geocoded: 3501 W SUNSET BLVD, LOS ANGELES, CA 90026: OK
Geocoded: 2300 PICO, SANTA MONICA, CA 90405: OK
Geocoded: 2300 PICO, SANTA MONICA, CA 90405: OK
Geocoded: 737 E ALTADENA AVE, ALTADENA, CA 91001: OK
Geocoded: 737 E ALTADENA AVE, ALTADENA, CA 91001: OK
Geocoded: 232 N LARCHMONT AV

Geocoded: 24575 COPPERHILL DR, SANTA CLARITA, CA 91354: OK
Geocoded: 24575 COPPERHILL DR, SANTA CLARITA, CA 91354: OK
Geocoded: 43559 W 10TH ST, LANCASTER, CA 93534: OK
Geocoded: 43559 W 10TH ST, LANCASTER, CA 93534: OK
Geocoded: 17404 BELLFLOWER BLVD STE B, BELLFLOWER, CA 90706: OK
Geocoded: 17404 BELLFLOWER BLVD STE B, BELLFLOWER, CA 90706: OK
Error geocoding 8830 APOLLO WAY # 116, DOWNEY, CA 90242: REQUEST_DENIED
Error geocoding 8830 APOLLO WAY # 116, DOWNEY, CA 90242: REQUEST_DENIED
Geocoded: 8830 APOLLO WAY # 116, DOWNEY, CA 90242: REQUEST_DENIED
Geocoded: 8830 APOLLO WAY # 116, DOWNEY, CA 90242: REQUEST_DENIED
Geocoded: 1841 REDONDO BEACH BLVD, GARDENA, CA 90247: OK
Geocoded: 1841 REDONDO BEACH BLVD, GARDENA, CA 90247: OK
Error geocoding 8150 GARVEY AVE # 117C, ROSEMEAD, CA 91770: REQUEST_DENIED
Error geocoding 8150 GARVEY AVE # 117C, ROSEMEAD, CA 91770: REQUEST_DENIED
Geocoded: 8150 GARVEY AVE # 117C, ROSEMEAD, CA 91770: REQUEST_DENIED
Geocoded: 8150 GARVEY AVE # 117C, ROSEMEAD,

Geocoded: 1251 3RD ST PROMENADE, SANTA MONICA, CA 90401: OK
Geocoded: 1251 3RD ST PROMENADE, SANTA MONICA, CA 90401: OK
Geocoded: 24621 COPPER HILL DR, SANTA CLARITA, CA 91354: OK
Geocoded: 24621 COPPER HILL DR, SANTA CLARITA, CA 91354: OK
Geocoded: 6815 FOOTHILL BLVD, TUJUNGA, CA 91042: OK
Geocoded: 6815 FOOTHILL BLVD, TUJUNGA, CA 91042: OK
Geocoded: 1123 ALOSTA AVE, AZUSA, CA 91702: OK
Geocoded: 1123 ALOSTA AVE, AZUSA, CA 91702: OK
Geocoded: 201 N LOS ANGELES ST, LOS ANGELES, CA 90012: OK
Geocoded: 201 N LOS ANGELES ST, LOS ANGELES, CA 90012: OK
Geocoded: 5452 E WHITTIER BLVD, COMMERCE, CA 90022: OK
Geocoded: 5452 E WHITTIER BLVD, COMMERCE, CA 90022: OK
Geocoded: 916 BURBANK BLVD STE H, BURBANK, CA 91506: OK
Geocoded: 916 BURBANK BLVD STE H, BURBANK, CA 91506: OK
Geocoded: 614 PACIFIC COAST HWY, WILMINGTON, CA 90744: OK
Geocoded: 614 PACIFIC COAST HWY, WILMINGTON, CA 90744: OK
Error geocoding 3500 OVERLAND AVE # 100, LOS ANGELES, CA 90034: REQUEST_DENIED
Error geocoding 3500 OVERLAND